<table style="width: 100%; border-style: none;">
<tr style="border-style: none">
<td style="border-style: none; width: 1%; text-align: left; font-size: 16px">Institut f&uuml;r Theoretische Physik<br /> Universit&auml;t zu K&ouml;ln</td>
<td style="border-style: none; width: 1%; font-size: 16px">&nbsp;</td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 16px">Prof. Dr. Simon Trebst<br />Christoph Berke</td>
</tr>
</table>
<hr>
<h1 style="font-weight:bold; text-align: center; margin: 0px; font-size: 30px; padding:0px;">Statistische Physik</h1>
<h1 style="font-weight:bold; text-align: center; margin: 0px; font-size: 30px; padding:0px;">Übungsblatt 3</h1>
<hr>
<h3 style="font-weight:bold; text-align: center; margin: 0px; font-size: 20px; padding:0px; margin-bottom: 20px;">Wintersemester 2020/21</h3>
<hr>

**Website** [http://www.thp.uni-koeln.de/trebst/Lectures/2020-StatPhys.shtml](http://www.thp.uni-koeln.de/trebst/Lectures/2020-StatPhys.shtml)

**Abgabe**:  Montag,23.11.2020, bis 10:00 Uhr

**Besprechung**:  Dienstag, 24.11.2020

**Name**: <font color="red">Bitte geben Sie ihren Namen an</font>

**Matrikelnummer**: <font color="red">Bitte geben Sie ihre Matrikelnummer an</font>

# Der zentrale Grenzwertsatz und beliebige Verteilungen $p(x)$

In dieser Aufgaben möchten wir den zentralen Grenzwertsatz im Bezug auf beliebige Verteilungen $p(x)$ diskutieren. Sie haben im Rahmen der Computerphysik bereits gelernt, wie Sie Zufallszahlen $x$ einer Verteilung $p(x)$ erzeugen können, jetzt möchten wir dies dazu benutzen den zentralen Grenzwertsatz zu prüfen.

### Konvertieren einer Funktion $f$ zu einer Verteilung $p$

Starten wir mit einer beliebigen Funktion $f(x)$ auf einem Intervall $[a,b]$. Wählen Sie für $f$ eine Funktion Ihrer Wahl, sowie geeignete $a$ und $b$ und plotten Sie den Kurvenverlauf mittels `PyPlot`.

*Hinweis*: Hier dürfen und sollen Sie wirklich kreativ werden, solange $f(x)>0$ auf dem Intervall gilt. Addieren und multiplizieren Sie gerne fleißig Terme Ihrer Wahl um möglichst interessante Kurvenverläufe zu erhalten. Wenn Sie nicht wissen, womit Sie anfangen sollen, benutzen Sie einfach $f(x) = x^4 - x^2 + 1/2$ sowie $a=0$ und $b=1$.

In [ ]:
using PyPlot

f(x) = x^4 - x^2 + 1/2
a    = 0
b    = 1

xvals = range(a, stop=b, length=100)
plot(xvals, f.(xvals))
ylim(0.0, maximum(f.(xvals))*1.05)
xlabel("x")
ylabel("f(x)")

Da für eine Verteilungsfunktion $p(x)$ u.A. gilt, dass diese normiert ist, müssen wir die Funktion $f(x)$ normieren. Wir suchen also einen Faktor $\alpha$, sodass

\begin{equation}
    \int_{a}^{b} \alpha f(x) dx = 1
\end{equation}

und damit $p(x) = \alpha f(x)$. Durch einfaches Umstellen obiger Gleichung erhalten wir

\begin{equation}
    \alpha^{-1} = \int_{a}^{b} f(x)
\end{equation}

was bedeutet, dass wir die Funktion $f$ auf dem Intervall $[a,b]$ integrieren müssen.

Nachfolgend haben wir für Sie bereits eine Funktion implementiert, die das Integral berechnet. Anschließend wird die normierte Funktion $f$, also unsere Wahrscheinlichkeitsverteilung $p$ geplottet.

In [ ]:
function integrate(f :: Function , a::Real,b::Real, vals::Integer=100000)
    xvals = range(a, stop=b, length=vals)
    fvals = f.(xvals)
    return sum(fvals)/(vals/(b-a))
end

In [ ]:
alpha = 1/integrate(f, a,b)

p(x) = alpha*f(x)

plot(xvals, p.(xvals))
ylim(0.0, maximum(p.(xvals))*1.05)
xlabel("x")
ylabel("p(x)")

### Erzeugung von $p$-verteilten Zufallszahlen

Wie Sie zweifelsfrei noch aus der Computerphysik wissen, stehen Ihnen im Prinzip zwei Möglichkeiten zur Verfügung um Zufallszahlen der Verteilung $p$ zu erzeugen:
1. Monte-Carlo / Metropolis Algorithmus
2. von-Neumansche Verwerfungsmethode

(die dritte Methode, die Inversionsmethode ist leider für *beliebige* Verteilungen $p$ nicht anwendbar)


Wir möchten im Folgenden die von-Neumansche Verwerfungsmethode verwenden. Dafür benötigen man eine einhüllende Funktion $\lambda h(x)$, für welche auf dem kompletten Intervall $[a,b]$ gilt, dass $p(x) < \lambda h(x)$. Wir möchten hier für $h(x)$ die Gleichverteilung benutzen, sodass wir schnell mittels `rand()` Zahlen dieser Verteilung ziehen können. Dies führt dazu, dass wir $\lambda$ leicht größer als das Maximum der Funktion $p$ auf dem Intervall $[a,b]$ wählen können. Das Maximum wird an dieser Stelle nicht aufwendig bestimmen, sondern einfach als der maximale Wert einer Liste von Funktionswerten auf dem Intervall $[a,b]$ gesetzt.

Mit diesen Zutaten haben wir für Sie jetzt die Verwerfungsmethode implementiert, und verwendet, um $n = 1.000.000$ Zufallszahlen der Verteilungsfunktion $p$ im Intervall $[a,b]$ zu erzeugen. Ein normiertes Histogram dieser Zufallszahlen kann mittels der `PyPlot` Funktion `hist(...,bins = 100, density=true)` geplottet werden. Die Verteilungsfunktion $p$ wird ebenfalls dargestellt, um zu zeigen, dass mit dem Histogram genau die Verteilungsfunktion getroffen wird. Sie haben jetzt $p$-verteilte Zufallszahlen!

In [ ]:
using Base.Threads

In [ ]:
function rand_vN_rejection(f::Function, a::Real,b::Real, lambda::Real)
    x = a + rand()*(b-a)
    while rand() > f(x)/lambda
        x = a + rand()*(b-a)
    end
    return x
end
function rand_vN_rejection(f::Function, a::Real,b::Real, lambda::Real, n::Integer)
    numbers = zeros(n)
    @threads for i in 1:n
        numbers[i] = rand_vN_rejection(f, a,b, lambda)
    end
    return numbers
end

In [ ]:
lambda = maximum(p.(xvals)) * 1.1

random_numbers = rand_vN_rejection(p, a,b, lambda, 1000000)

hist(random_numbers, bins=100, density=true, label="numbers")
plot(xvals, p.(xvals), label="p(x)")
xlim(a - (b-a)*0.05, b + (b-a)*0.05)
xlabel("x")
ylabel("p(x)")
legend()

### a) Zentraler Grenzwertsatz - (1) Scharfe Verteilungen

Da Sie jetzt in der Lage sind, $p$-verteilte Zufallszahlen zu erzeugen, können wir dazu übergehen, den zentralen Grenzwertsatz zu untersuchen. In diesem ersten Teil sollen Sie zeigen, dass die Verteilung des Mittelwerts von $N$ $p$-verteilten Zahlen gegen einen Delta-Peak am Erwartungswert der Verteilung $p$ konvergiert.

Erzeugen Sie Histogramme des Mittelwerts 
\begin{equation}
    X_N = \frac{1}{N}\sum_{i=1}^N x_i
\end{equation}

für verschiedene Werte von $N$ und plotten Sie alles in ein Diagram. Was können Sie erkennen?

### b) Zentraler Grenzwertsatz - (2) Konvergenz gegen Gausverteilung

Im zweiten Teil der Untersuchung des zentralen Grenzwertsatzes möchten wir auf die Konvergenz der Verteilung der Mittelwerte $X_N$ gegen eine Gausverteilung zu sprechen kommen. Wir wissen aus der Vorlesung, dass die Breite des in c) ermittelten Peaks bei $\sigma / \sqrt{N}$ liegt, wobei $\sigma^2 = \text{var}(X_N)$.

Erzeugen Sie erneut Mittelwerte
\begin{equation}
    X_N = \frac{1}{N}\sum_{i=1}^N x_i
\end{equation}
aber plotten Sie dieses Mal Histogramme der Verteilung von
\begin{equation}
    \sqrt{N}\frac{X_N - \langle x \rangle}{\sigma}
\end{equation}
Sie können den Erwartungwert $\langle x \rangle$ als Mittelwert einer großen Anzahl Samples berechnen. Benutzen Sie außerdem z.B. die Funktion `var` im Paket `Statistics` um aus der gleichen Menge Zahlen die Varianz der Verteilung $p$ nährungsweise zu bestimmen.

Plotten Sie erneut Histogramme für verschiedene $N$ in einem Diagramm und beurteilen Sie inwiefern sich die Form der Verteilung der Standard-Gauskurve annährt. Zeichnen Sie letztere ebenfalls ein.

In [ ]:
using Statistics